In [53]:
!pip install kaggle
!pip install pandas
!pip install seaborn

In [54]:
!kaggle datasets download -d wenruliu/adult-income-dataset

    

401 - Unauthorized


In [55]:
!unzip -o adult-income-dataset.zip

'unzip' is not recognized as an internal or external command,
operable program or batch file.


In [56]:
import pandas as pd
df=pd.read_csv('adult-income-dataset.csv')
df


age     workclass  fnlwgt     education  educational-num  \
0       25       Private  226802          11th                7   
1       38       Private   89814       HS-grad                9   
2       28     Local-gov  336951    Assoc-acdm               12   
3       44       Private  160323  Some-college               10   
4       18             ?  103497  Some-college               10   
...    ...           ...     ...           ...              ...   
48837   27       Private  257302    Assoc-acdm               12   
48838   40       Private  154374       HS-grad                9   
48839   58       Private  151910       HS-grad                9   
48840   22       Private  201490       HS-grad                9   
48841   52  Self-emp-inc  287927       HS-grad                9   

           marital-status         occupation relationship   race  gender  \
0           Never-married  Machine-op-inspct    Own-child  Black    Male   
1      Married-civ-spouse    Farming-fishing      Husband  White    Male   
2      Married-civ-spouse    Protective-serv      Husband  White    Male   
3      Married-civ-spouse  Machine-op-inspct      Husband  Black    Male   
4           Never-married                  ?    Own-child  White  Female   
...                   ...                ...          ...    ...     ...   
48837  Married-civ-spouse       Tech-support         Wife  White  Female   
48838  Married-civ-spouse  Machine-op-inspct      Husband  White    Male   
48839             Widowed       Adm-clerical    Unmarried  White  Female   
48840       Never-married       Adm-clerical    Own-child  White    Male   
48841  Married-civ-spouse    Exec-managerial         Wife  White  Female   

       capital-gain  capital-loss  hours-per-week native-country income  
0                 0             0              40  United-States  <=50K  
1                 0             0              50  United-States  <=50K  
2                 0             0              40  United-States   >50K  
3              7688             0              40  United-States   >50K  
4                 0             0              30  United-States  <=50K  
...             ...           ...             ...            ...    ...  
48837             0             0              38  United-States  <=50K  
48838             0             0              40  United-States   >50K  
48839             0             0              40  United-States  <=50K  
48840             0             0              20  United-States  <=50K  
48841         15024             0              40  United-States   >50K  

[48842 rows x 15 columns]

In [57]:
df['income_if_<=50k'] = df['income'].apply(lambda x: True if x == '<=50K' else False)
df['if_male'] = df['gender'].apply(lambda x: True if x == 'Male' else False)
df['income_if_<=50k']= df['income_if_<=50k'].astype(int)
df['if_male']= df['if_male'].astype(int)


In [58]:
#usunięcie nie pełnych danych 
df = df[df.workclass != '?']
df = df.reset_index()

In [59]:
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
X, y = df[['age']], df['income_if_<=50k']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=37)
n_samples, n_features = X.shape

In [60]:
X_train = np.array(X_train).reshape(-1,1)
X_test = np.array(X_test).reshape(-1,1)
y_train = np.array(y_train).reshape(-1,1)
y_test = np.array(y_test).reshape(-1,1)

In [61]:
sc = StandardScaler()
X_train = sc.fit_transform(X_train)
X_test = sc.fit_transform(X_test)



In [62]:
import torch
torch.from_file
X_train = torch.from_numpy(X_train.astype(np.float32))
X_test = torch.from_numpy(X_test.astype(np.float32))
y_train = torch.from_numpy(y_train.astype(np.float32))
y_test = torch.from_numpy(y_test.astype(np.float32))

y_train = y_train.view(y_train.shape[0], 1)
y_test= y_test.view(y_test.shape[0], 1)


In [63]:
import torch.nn as nn
class LogisticRegresion(nn.Module):
    def __init__(self, n_input_featuers):
        super(LogisticRegresion, self).__init__()
        self.linear = nn.Linear(n_input_featuers, 1)
    
    def forward(self, x):
        y_predicted = torch.sigmoid(self.linear(x))
        return y_predicted

model = LogisticRegresion(n_features)

In [64]:
criterion = nn.BCELoss()
optimizer = torch.optim.SGD(model.parameters(), lr=0.01)

In [65]:
num_epochs = 1500
for epoch in range(num_epochs):
    y_predicted = model(X_train)
    loss = criterion(y_predicted,y_train)
    loss.backward()
    optimizer.step()
    optimizer.zero_grad()

    if (epoch%100==0):
        print(f'epoch:{epoch+1},loss = {loss.item():.4f}')

epoch:1,loss = 1.0032
epoch:101,loss = 0.8295
epoch:201,loss = 0.7194
epoch:301,loss = 0.6511
epoch:401,loss = 0.6088
epoch:501,loss = 0.5823
epoch:601,loss = 0.5656
epoch:701,loss = 0.5548
epoch:801,loss = 0.5478
epoch:901,loss = 0.5431
epoch:1001,loss = 0.5400
epoch:1101,loss = 0.5378
epoch:1201,loss = 0.5363
epoch:1301,loss = 0.5353
epoch:1401,loss = 0.5346


In [66]:
with torch.no_grad():
    y_predicted = model(X_test)
    y_predicted_cls = y_predicted.round()
    acc = y_predicted_cls.eq(y_test).sum()/float(y_test.shape[0])
    print(f'{acc:.4f}')

0.7395


In [72]:
result = open("result_pytorch",'w+')
result.write(f'acc:{acc:.4f}')

10